## answers 13: the adventure of the three trees

In [1]:
import numpy as np

### 1. implement code for simulating sequences down a tree

First, let's instantiate the three pset trees in a Python data structure.

I'll write a function `specify_trees()` that returns the three trees as a list. Tree T0 is `T[0]`, and so on. 

Each tree is a list of 2n-1 nodes numbered 0..2n-2 for n taxa. Nodes 0..n-1 are the n observed leaf taxa. Nodes n..2n-2 are the internal nodes. Node 2n-2 is the root. 

Each node is set to either `None` (for leaf taxa that have no children) or a tuple of (left_child, right_child). Then each child is itself a tuple of (child_idx, branch_len) to identify which node is the child, and the length of the branch to it in substitutions/site.

In [2]:
def specify_trees():
    r"""
    Create the three trees for the problem ("pset trees").

    Args:
      (none)

    Returns:
      List of three tree structures.

    Trees[0]  = true tree... ML, NJ will favor
    Trees[1]  = long branch attraction tree... UPGMA, parsimony will favor
    Trees[2]  = the remaining topology...  no method will favor

         .6            .6             .6
        / \           / \            / \
       .4  .5        .4  .5         .4  .5
      /|   |\       /|   |\        /|   |\
     / 0   1 \     0 1   | \      / 0   1 \
    2         3          2  3    3         2
  
     T0 = true       T1 = LBA      T2 = other

    A (rooted) tree is a list of 2N-1 nodes, 0..2N-2. 
       Nodes 0..N-1 are the taxa on the leaves.
       These leaf nodes are set to None: they have no children.
       Nodes N..2N-2 are the internal nodes. 2N-2 is the root.
    Each internal node is a tuple of (left_child, right_child).
    Each child is a tuple of (idx, branchlen).
       idx = 0..2N-2 index of child node.
       branchlen = branch length to that child, in substitutions/site
        
    A branch length in units of substitutions/site is 3 \alpha t in Jukes-Cantor:
    so \alpha t = branchlen/3, when we go to parameterize substitution probs from
    these branch lengths.
    """

    #         --- leaf taxa (0..3) ----  - internal node (4) -  - internal node (5) -  --- root node (6) ---
    Trees = [ [ None, None, None, None,  ((2, 0.6), (0, 0.1)),  ((1, 0.1), (3, 0.6)),  ((4, 0.05), (5, 0.05))],
              [ None, None, None, None,  ((0, 0.1), (1, 0.1)),  ((2, 0.6), (3, 0.6)),  ((4, 0.05), (5, 0.05))],
              [ None, None, None, None,  ((3, 0.6), (0, 0.1)),  ((1, 0.1), (2, 0.6)),  ((4, 0.05), (5, 0.05))] ]
    return Trees

Now I want a function `sample_sequences()` to generate sequences down a tree.

I'll store my multiple sequence alignment as a nseq x L ndarray, with DNA residues digitized as values 0..3 representing A..T.

I'll write a function `sample_descendant()` to generate one child sequence from one ancestor, and  a function `p_jukescantor()` to give me the $P(b \mid a,t)$ substitution probabilities as a matrix `P[a][b]`, given a branch length.

A potentially tricky bit here is that in a Jukes-Cantor model, the expected number of substitutions/site is $3 \alpha t$. So if we're given a branch length $b_i$ in units of substitutions/site, $\alpha t = \frac{b_i}{3}$. 

In [3]:
def p_jukescantor(branchlen):
    r"""Create Jukes/Cantor P(b|a,t) given branch len in subst/site.

    Args:
        branchlen (float >= 0) : branch length in subst/site

    Returns:
        P (ndarray, 4x4) : P[a,b] is P(b|a,t), where t is branchlen/3
    """
    rp = 1/4 + 3/4 * np.exp(-4/3 * branchlen)
    sp = 1/4 - 1/4 * np.exp(-4/3 * branchlen)
    P = np.array([[ rp, sp, sp, sp ],
                  [ sp, rp, sp, sp ],
                  [ sp, sp, rp, sp ],
                  [ sp, sp, sp, rp ]])
    return P

In [4]:
def sample_descendant(rng, Y, P):
    r"""Sample a descendant sequence X, given ancestor Y.

    Args:
        rng              : numpy RNG
        Y (ndarray, L)   : ancestral sequence
        P (ndarray, 4x4) : P[a,b] is P(b|a,t); t is blen/3 for Jukes/Cantor

    Returns:
        X (ndarray, L)   : descendant sequence
    """
    L = len(Y)       # ancestral sequence length
    K = len(P[0])    # alphabet size

    X = np.zeros( L, dtype=int)
    for i in range(L):
        X[i] = rng.choice(K, p=P[Y[i]])
    return X


In [5]:
def sample_sequences(rng, T, L):
    r"""
    Sample a multiple seq alignment down a tree.

    Args:
        rng  : numpy RNG
        T    : rooted tree structure to generate down
        L    : length of sequences to generate

    Returns:
        msa  : (nnodes x L) ndarray of digital seqs.
               Values are 0..3 for digitized DNA residues A..T.
               Rows 0..ntaxa-1 are seqs at the leaves.
               Rows ntaxa..nnodes-1 are ancestral seqs at internal nodes
               Row nnodes-1 is the last common ancestor, at root.

    General; works on any tree T, not just a pset tree.
    """
    nnodes = len(T)
    ntaxa  = (nnodes + 1)//2
    rooty  = nnodes-1

    msa = np.zeros( (nnodes, L), dtype=int)   # msa[0..n-1] = leaves; msa[n..2n-2] = internal; msa[2n-2] = root

    msa[rooty] = rng.integers(0, 4, L)        # generate a random ancestral digital DNA sequence at the root
    stack    = [ rooty ]                      # initialize a stack with the root idx on it
    while len(stack) > 0:                     # iterate through internal nodes, root to leaves:
        a      = stack.pop()                  # a = idx of ancestor node. We know a is internal because we only push internal nodes
        for (b, blen) in T[a]:                
            P    = p_jukescantor(blen)        # branch len is in subst/site: 3at in jukes-cantor time t units
            msa[b] = sample_descendant(rng, msa[a], P)
            if b >= ntaxa: stack.append(b) 
    return msa

### 2. implement mini UPGMA

For the distance-based methods, we need to first calculate a pairwise distance matrix $d_{ij}$ for all pairs of sequences $(i,j)$. 

I'll do that in two pieces. First, a function to calculate the Jukes-Cantor distance for one pair of sequences; second, a function to run that over all pairs $(i,j)$.

A potentially tricky part here is what happens if the observed fractional difference (the so-called "p distance") between two sequences is $\geq$ 0.75. This can happen by stochastic chance for finite-length DNA sequences that are very distantly related; for example for taxa (2,3) here. The Jukes-Cantor distance is then undefined. We can catch this case and assign an infinite distance, but then we'll create other problems with subtracting infinities and getting NaN's. It suffices as a hack here to just assign a ridiculously large but finite distance: here I'm assigning 100.

In [6]:
def dist_jukescantor(dsq1, dsq2):
    r"""Calculate Jukes/Cantor distance between two aligned seqs.

    Args:
        dsq1 (ndarray, L) : digital sequence 1, from ungapped MSA
        dsq2 (ndarray, L) : digital sequence 2

    Returns:
        (float, >= 0) : estimated J/C distance in subst/site

    Let f = fractional difference = nsubst / (nsubst + nid).
    Then d = -3/4 log(1 - 4/3 f).

    When f >= 0.75, Jukes/Cantor distance is undefined, but f >= 0.75
    can easily happen for distantly related sequences. To handle
    this case, we set an arbitrarily large distance of 100. Though
    arbitrary, this is better than setting an element to infinity,
    because subsequent operations on infinite distances can result
    in NaN's and undefined bad behavior.

    d is a branch length in subst/site.
    """
    nid, nsubst = 0, 0
    alen        = len(dsq1)
    assert(len(dsq2) == alen)
    
    for a,b in zip(dsq1, dsq2):
        if a == b: nid    += 1
        else:      nsubst += 1

    fsubst = nsubst / (nid + nsubst)
    if fsubst < 0.75: d = -3/4 * np.log(1 - fsubst*4/3)
    else:             d = 100.          # arbitrary large distance
    return d 

In [7]:
def dist_matrix(msa):
    r"""Calculate Jukes/Cantor distance matrix d_ij for all seq pairs in msa.

    Args:
        msa (ndarray, nseq x L) : digitized ungapped mult seq alignment

    Returns:
       (ndarray, nseq x nseq) : d_ij for all pairs of seqs

    The msa we generate for the pset contains both leaf taxa and
    internal ancestors. We usually only need to calculate d_ij for
    the taxa. Therefore this function is usually called as something
    like `dist_matrix(msa[:ntaxa])`.

    d_ij is symmetric (d[i,j] == d[j,i]) with 0's down diagonal (d[i,i] = 0).
    """
    nseq   = len(msa)
    ncol   = len(msa[0])

    d = np.zeros( (nseq, nseq) )   # diagonal i=j initialized to zero here. Others replaced below.
    for i in range(nseq):
        for j in range(i+1, nseq):
            d[i,j] = d[j,i] = dist_jukescantor(msa[i], msa[j])
    return d

Now I'll write a function `best_distance_tree()` that I'll share between mini UPGMA and mini NJ, where I can use the same function to finding argmin (i,j) in the $d_{ij}$ matrix directly (for UPGMA) or find argmin (i,j) in the NJ modified $D_{ij}$ matrix). Then, given the best (i,j), I know which unrooted tree topology is supported.

A potentially tricky thing here is, what to do about ties, when more than one (i,j) pair has the same minimum distance. Here I go to the trouble of randomly choosing one of the optimal solutions.

In [8]:
def best_distance_tree(rng, D):
    r"""Find which pset tree is supported by distance matrix D.

    Args:
        rng : NumPy RNG, used for randomly breaking ties
        D (ndarray, ntaxa x ntaxa) : UPGMA d_ij or NJ D_ij

    Returns:
        (int) 0|1|2 : which pset tree is supported, based on min D_ij

    D is either the unmodified d_ij distance matrix (UPGMA) or the
    modified D_ij matrix for neighbor-joining.

    Identify which pair i,j would be joined first, by finding
    argmin_{ij} D_ij.

    If more than one i,j pair has the same minimum cost, choose one 
    randomly.

    From that first pair (i,j), identify which of the three pset tree
    topologies would be the end result of the distance method. This
    works because there are only three unrooted tree topologies for
    4 taxa. 

    Rooting is ignored for this purpose. The three pset tree
    topologies are treated as unrooted topologies. UPGMA finds rooted
    topologies, and there are 15 possible rooted topologies for 4
    taxa, but we only compare the UPGMA result against the pset trees
    as unrooted topologies.
    """
    (ntaxa,ntaxa) = D.shape
    assert(ntaxa == 4)    # Not general; requires that we're using pset trees.

    # Identify *a* argmin_ij D_ij.
    # There may be more than one; if so, choose randomly.
    #
    # We can almost just do np.argmin(d) (and unravel that flattened
    # idx) but we need to not count the diagonal where d_ii = 0, and
    # we need to break any ties randomly.
    #
    # So: choose a random min i,j element from upper triangular d
    # This is a carefully crafted NumPy incantation:
    #    np.triu_indices gives us indices for upper triangular part of d_ij
    #    np.min gives us the min value in it
    #    np.flatnonzero gives array of one or more element indices in iu that have that min
    #    rng.choice chooses one of them randomly, and sets that idx to k
    #    best (i,j) is iu[0][k], iu[1][k]
    # then we call best_tree to turn the first neighbor pair (i,j) into
    # the index of the pset tree that that implies.
    # 
    iu      = np.triu_indices(ntaxa,1)
    k       = rng.choice(np.flatnonzero(D[iu] == np.min(D[iu])))
    i,j     = iu[0][k],iu[1][k]

    if   (i,j) == (0,1): best_tree = 1
    elif (i,j) == (0,2): best_tree = 0
    elif (i,j) == (0,3): best_tree = 2
    elif (i,j) == (1,2): best_tree = 2
    elif (i,j) == (1,3): best_tree = 0
    elif (i,j) == (2,3): best_tree = 1
    else:                exit("that can't happen")
    return best_tree

Now "mini UPGMA" simply means find the minimum distance $d_{ij}$, and then figure out which unrooted tree topology results from joining that (i,j) pair first.

In [9]:
def mini_upgma(rng, msa):
    r"""Determine which pset tree would be chosen by UPGMA.

    Args:
        rng:                       numpy RNG. Used to break any ties.
        msa (ndarray, ntaxa x L):  digital MSA for observed leaf seqs

    Return:
        (int) 0|1|2 : which pset tree is chosen by UPGMA

    We only need to do the first iteration of UPGMA, choosing 
    min_{i,j} d_ij, to know which pset tree UPGMA finds.
    
    Typically called as `mini_upgma(rng, msa[:ntaxa])` since our
    sampled MSAs include both leaf seqs and internal ancestors.

    Assumes the 3 rooted pset trees are the only options for tree
    topology, so ntaxa==4.
    """
    ntaxa = len(msa)
    d     = dist_matrix(msa)
    return best_distance_tree(rng, d)

### 3. implement mini NJ

Now mini NJ is easy too. We just process the $d_{ij}$ matrix through NJ's adjusted $D_{ij} = d_{ij} - (r_i + r_j)$, with $r_i = \frac{1}{n-2} \sum_{k=0}^{n-1} d_{ik}$ for $n$ taxa.

In [10]:
def mini_nj(rng, msa):
    r"""Determine which pset tree would be chosen by neighbor-joining.

    Like mini_upgma() above, but with neighbor-joining.
    """
    ntaxa = len(msa)

    d  = dist_matrix(msa)
    r  = np.sum(d, axis=1) / (ntaxa-2)   # rows or columns is same, d_ij is symmetric

    # The neighbor-joining D matrix: D_ij = d_ij - (r_i + r_j)
    # where r_i = \sum_{k} d_{ik} for all taxa k
    #
    D  = np.zeros( d.shape )
    for i in range(ntaxa):
        for j in range(i+1,ntaxa):
            D[i,j] = D[j,i] = d[i,j] - r[i] - r[j]

    return best_distance_tree(rng, D)

### 4. implement Fitch parsimony

The trickiest bit of this (and ML) is just dealing with my tree data structure. For interior nodes $y = n..2n-2$, `T[y]` is a tuple of data for the children of node $y$; `T[y][0]` and `T[y][1]` are the two elements of that tuple, the data for left and right child (also a tuple); `T[y][w][0]` is the index of a child of $y$, where $w=0$ for left child and $w=1$ for right.

In [11]:
def parsimony(T, msa):
    r"""Fitch parsimony: calculate cost of tree topology T for input MSA.

    Args:
        T (list of <nnodes> tree nodes): proposed tree topology
        msa (ndarray, ntaxa x L):        ungapped digital MSA

    Returns:
        (int) cost of tree T.

    The number of taxa and nodes in T are both determined from T.

    msa can contain more aligned seqs (we generate MSA's that also
    contain the ancestors, in rows ntaxa..nnodes-1, but they won't
    be accessed. Only rows 0..ntaxa-1 of <msa> are accessed.
    """
    nnodes = len(T)
    ntaxa  = (nnodes + 1) // 2
    ncol   = len(msa[0])

    cost   = 0
    S = [set() for _ in range(nnodes)]   # We'll construct a set of residues at each interior node...
    for i in range(ncol):                # ... for each position i (aligned column) in seq alignment <msa>...
        for y in range(ntaxa):
            S[y] = { msa[y,i] }
        for y in range(ntaxa, nnodes):
            lc = T[y][0][0]
            rc = T[y][1][0]
            if len(S[lc] & S[rc]) > 0: S[y] = S[lc] & S[rc]
            else:                      S[y] = S[lc] | S[rc]; cost += 1
    return cost

### 5. implement Felsenstein maximum likelihood

The Felsenstein "peeling" algorithm is a dynamic programming algorithm that feels like a cross between the parsimony algorithm and the HMM forward algorithm that we've seen earlier in the course.

In [12]:
def maximum_likelihood(T, msa):
    r"""Felstenstein ML algorithm: calculate log likelihood for tree T

    Args:
        T (list of <nnodes> tree nodes): proposed tree topology
        msa (ndarray, ntaxa x L):        ungapped digital MSA

    Returns:
        (float) log likelihood of tree T. Larger is better.
    """
    nnodes = len(T)
    ntaxa  = (nnodes + 1) // 2
    ncol   = len(msa[0])

    # Precompute P(b|a,t) for each child branch
    Prob = []
    for y in range(ntaxa):         Prob.append(None)
    for y in range(ntaxa, nnodes): Prob.append( (p_jukescantor(T[y][0][1]), p_jukescantor(T[y][1][1])) )  # left, right branch lens

    logL = 0.0
    # Sum -logL over each column in the alignment independently:
    for i in range(ncol):
        # Initialize with P(L_y | a) at leaves
        L = np.zeros( (nnodes, 4) )        
        for y in range(ntaxa):  L[y,msa[y,i]] = 1.0

        for y in range(ntaxa, nnodes):
            lc,rc = T[y][0][0], T[y][1][0]
            lP,rP = Prob[y][0], Prob[y][1]
            for a in range(4):
                lprob,rprob = 0.0,0.0
                for b in range(4):
                    lprob += L[lc,b] * lP[a,b]
                    rprob += L[rc,b] * rP[a,b]
                L[y,a] = lprob * rprob

        totprob = 0.
        for a in range(4):
            totprob += L[nnodes-1,a] * 0.25   # that's a \pi_a = 0.25 uniform prior at the root
        logL += np.log(totprob)               # summing log likelihood over positions/columns i
    return logL


### 6. do Adler's suggested experiment

Now we're ready to do the simulation experiment.

In [13]:
rng            = np.random.default_rng()
nruns          = 100
msalen_choices = [ 20, 100, 500, 2000]

Trees  = specify_trees()
ntrees = len(Trees)
nnodes = len(Trees[0])
ntaxa  = (nnodes + 1) // 2
costs  = np.empty(ntrees)    # parsimony costs
logL   = np.empty(ntrees)    # ML log likelihoods

wins = {
    'upgma'     : np.zeros( (len(msalen_choices), ntrees), dtype=int),
    'nj'        : np.zeros( (len(msalen_choices), ntrees), dtype=int),
    'parsimony' : np.zeros( (len(msalen_choices), ntrees), dtype=int),
    'ml'        : np.zeros( (len(msalen_choices), ntrees), dtype=int),
}

for e, msalen in enumerate(msalen_choices):
    for r in range(nruns):
        msa  = sample_sequences(rng, Trees[0], msalen)

        # UPGMA
        best_tree = mini_upgma(rng, msa[:ntaxa])
        wins['upgma'][e,best_tree] += 1
 
        # NJ
        best_tree = mini_nj(rng, msa[:ntaxa])
        wins['nj'][e,best_tree] += 1
            
        # Parsimony
        for t in range(ntrees):
            costs[t]  = parsimony(Trees[t], msa[:ntaxa])
        best_tree = rng.choice(np.flatnonzero(costs == np.min(costs)))
        wins['parsimony'][e,best_tree] += 1

        # ML
        for t in range(ntrees):
            logL[t]  = maximum_likelihood(Trees[t], msa[:ntaxa])
        best_tree = rng.choice(np.flatnonzero(logL == np.max(logL)))
        wins['ml'][e,best_tree] += 1

for method in wins.keys():
    print(f'{method}:')
    print('{:>6s} {:>6s} {:>6s} {:>6s}'.format('len', 'T0', 'T1', 'T2'))
    for e, msalen in enumerate(msalen_choices):
        print('{:6d} {:6d} {:6d} {:6d}'.format(msalen, wins[method][e,0], wins[method][e,1], wins[method][e,2]))
    print('')

upgma:
   len     T0     T1     T2
    20     11     85      4
   100      0    100      0
   500      0    100      0
  2000      0    100      0

nj:
   len     T0     T1     T2
    20     55     24     21
   100     78     20      2
   500     95      5      0
  2000    100      0      0

parsimony:
   len     T0     T1     T2
    20     43     36     21
   100     39     56      5
   500     39     61      0
  2000     22     78      0

ml:
   len     T0     T1     T2
    20     57     21     22
   100     87      7      6
   500    100      0      0
  2000    100      0      0



UPGMA systematically infers the wrong tree, T1. That's because the closest pair of sequences (by total summed branch length on the true tree T0) is the pair (0,1), which differ by 0.3 substitutions/site, but they aren't neighbors on the T0 tree topology. The true tree is additive but not ultrametric. It violates UPGMA's assumption that the tree is ultrametric (all taxa equidistant from the root). 

Parsimony, perhaps surprisingly, also systematically infers the wrong tree T1, but for a different reason. This artifact is called "long branch attraction". In the four-taxon MSA, the only "phylogenetically informative" sites (alignment columns) are those where two sequences have an identical residue, and the other two sequences have a different identical residue, in what I'll call a 2:2 pattern:

* if there are no substitutions in any sequence (all four residues identical), all trees give a cost of 0
* if there is 1 substitution in one sequence (3:1), all trees give a cost of 1
* if the pattern is 2:2, then the tree that puts these pairs together has cost 1, and other trees have cost 2
* if the pattern is 2:1:1, then all trees have cost 2 (not intuitive, but true)
* if the pattern is 1:1:1:1, all trees have cost 3

So if we happen to convergently generate the same substitution independently twice on the branches down to 2 and 3, without making any substitutions on the way to 0 and 1, that will look like support for tree T1 (which will explain those two substitutions as one event). The long branches to 2 and 3 increase the chances of this happening. 

This typically requires a fairly unusual tree, with unbalanced branch lengths that are long enough to have a high chance of convergent substitutions. But even a toy example like this (admittedly a carefully crafted one) can illustrate the artifact.

ML is statistically consistent, meaning that if we generate data from the substitution probability model and use the same substitution model for inference, we will infer the correct tree, in the limit of infinite sites. We see it quickly converge to correctly inferring T0 here. Of course, we don't know the real substitution process for real biological data. Whether ML infers correct trees for real data is a different matter. We typically don't have the compute power to fully explore all trees, and our substitution models are oversimplified relative to real sequence evolution.

Neighbor-joining works too! It sometimes gets a weird rap in the literature that I don't understand, perhaps because it's "just" a distance method and people lump it in with other distance methods like UPGMA. Neighbor-joining is statistically consistent and correctly infers the true tree, if the tree has additive distances. Additivity is not an unusual thing. When we use probabilistic models like Jukes-Cantor or Kimura or Hashegawa-Kishino-Yano to infer distances from observed alignments, we're inferring additive distances. 

### closing formalities

In [14]:
%load_ext watermark
%watermark -v -m -p jupyter,numpy,matplotlib

Python implementation: CPython
Python version       : 3.12.5
IPython version      : 8.26.0

jupyter   : 1.0.0
numpy     : 2.1.0
matplotlib: 3.9.2

Compiler    : Clang 13.0.0 (clang-1300.0.29.30)
OS          : Darwin
Release     : 23.6.0
Machine     : x86_64
Processor   : i386
CPU cores   : 16
Architecture: 64bit



[That's it!](https://en.wikipedia.org/wiki/So_Long,_and_Thanks_for_All_the_Fish)  Enjoy your winter break. Thanks for all the work you put into MCB112.